# BLISS AstroPy Affiliate Package Tutorial

## Introduction

Bayesian Light Source Separator (BLISS) is a Bayesian method for deblending and cataloging light sources.

## Installation

In [1]:
%env BLISS_HOME=/home/zhteoh/730-astropy-integration

env: BLISS_HOME=/home/zhteoh/730-astropy-integration


In [2]:
!pip install -e $BLISS_HOME

Obtaining file:///home/zhteoh/730-astropy-integration
  Installing build dependencies ... done
  Checking if build backend supports build_editable ... done
  Getting requirements to build editable ... done
  Preparing editable metadata (pyproject.toml) ... done
  Building editable for bliss-deblender (pyproject.toml) ... done
  Created wheel for bliss-deblender: filename=bliss_deblender-0.1.2-py3-none-any.whl size=4250 sha256=718c133f465dfd758fb1563ff1b26c8f6afc4497e997a35992f5c1ae00d43289
  Stored in directory: /tmp/pip-ephem-wheel-cache-x5uyc7s4/wheels/6e/ff/3a/b3c8dc9273fa82437c76778098de2f5c5c660d410e2f8504bc
Successfully built bliss-deblender
  Attempting uninstall: bliss-deblender
    Found existing installation: bliss-deblender 0.1.2
    Uninstalling bliss-deblender-0.1.2:
      Successfully uninstalled bliss-deblender-0.1.2


# Tutorial

## Train the model

### Generate synthetic image data

In [3]:
from bliss.api import generate

In [4]:
generate(
    n_batches=3, 
    batch_size=64, 
    max_images_per_file=128, 
    cached_data_path="/data/scratch/zhteoh/730-tutorial/dataset"
)

Data will be saved to /data/scratch/zhteoh/730-tutorial/dataset


Generating and writing cached dataset files: 100%|██████████| 2/2 [01:52<00:00, 56.17s/it]


#### Pass additional custom configuration parameters

In [5]:
generate(
    n_batches=3,  # required
    batch_size=64,  # required
    max_images_per_file=128,  # required
    cached_data_path="/data/scratch/zhteoh/730-tutorial/dataset",  # required
    simulator={"prior": {"mean_sources": 0.02}},  # optional
    generate={"file_prefix": "dataset"},  # optional
)

Data will be saved to /data/scratch/zhteoh/730-tutorial/dataset


Generating and writing cached dataset files: 100%|██████████| 2/2 [00:29<00:00, 14.70s/it]


In [6]:
# Check that the dataset is generated
!ls /data/scratch/zhteoh/730-tutorial/dataset
!du -sh /data/scratch/zhteoh/730-tutorial/dataset
# !cat /data/scratch/zhteoh/730-tutorial/dataset/hparams.yaml

import torch
with open("/data/scratch/zhteoh/730-tutorial/dataset/dataset_0.pt", "rb") as f:
    dataset = torch.load(f)
print(len(dataset))
print(dataset[0]["images"].shape)

dataset_0.pt  dataset_1.pt  hparams.yaml
18M	/data/scratch/zhteoh/730-tutorial/dataset
128
torch.Size([1, 80, 80])


### Train the model

In [7]:
from bliss.api import train

#### Without pretrained weights

In [8]:
train(
    weight_save_path="/data/scratch/zhteoh/730-tutorial/output/tutorial_encoder/0.pt",
)

Global seed set to 42

                 from  n    params  module                                  arguments                     
  0                -1  1      3328  yolov5.models.common.Conv               [2, 64, 5, 1]                 
  1                -1  3     12672  yolov5.models.common.Conv               [64, 64, 1, 1]                
  2                -1  1     73984  yolov5.models.common.Conv               [64, 128, 3, 2]               
  3                -1  1    147712  yolov5.models.common.Conv               [128, 128, 3, 1]              
  4                -1  1    295424  yolov5.models.common.Conv               [128, 256, 3, 2]              
  5                -1  6   1118208  yolov5.models.common.C3                 [256, 256, 6]                 
  6                -1  1   1180672  yolov5.models.common.Conv               [256, 512, 3, 2]              
  7                -1  9   6433792  yolov5.models.common.C3                 [512, 512, 9]                 
  8           

Sanity Checking: 0it [00:00, ?it/s]

Generating fixed validation set: 100%|██████████| 10/10 [04:45<00:00, 28.59s/it]


Training: 0it [00:00, ?it/s]

Unexpected exception formatting exception. Falling back to standard exception


Traceback (most recent call last):
  File "/home/zhteoh/730-astropy-integration/.venv/lib/python3.10/site-packages/IPython/core/interactiveshell.py", line 3460, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/tmp/ipykernel_2025915/1460248005.py", line 1, in <module>
    train(
  File "/home/zhteoh/730-astropy-integration/bliss/api.py", line 127, in train
  File "/home/zhteoh/730-astropy-integration/bliss/train.py", line 76, in train
    model_checkpoint = torch.load(checkpoint_callback.best_model_path, map_location="cpu")
  File "/home/zhteoh/730-astropy-integration/.venv/lib/python3.10/site-packages/torch/serialization.py", line 771, in load
    with _open_file_like(f, 'rb') as opened_file:
  File "/home/zhteoh/730-astropy-integration/.venv/lib/python3.10/site-packages/torch/serialization.py", line 270, in _open_file_like
    return _open_file(name_or_buffer, mode)
  File "/home/zhteoh/730-astropy-integration/.venv/lib/python3.10/site-packages/torch/serializ

#### With pretrained weights

Download our relevant pretrained weights for your sky survey.

In [9]:
from bliss.api import load_pretrained_weights_for_survey

import os
assert os.path.exists("/data/scratch/zhteoh/730-tutorial/pretrained_weights")

load_pretrained_weights_for_survey(
    survey="sdss",
    pretrained_weights_path="/data/scratch/zhteoh/730-tutorial/pretrained_weights/sdss_pretrained.pt",
)

#### Train on cached generated disk dataset

In [10]:
from bliss.api import train_on_cached_data

In [11]:
train_on_cached_data(
    weight_save_path="/data/scratch/zhteoh/730-tutorial/output/tutorial_encoder/0.pt",
    cached_data_path="/data/scratch/zhteoh/730-tutorial/dataset",
    train_n_batches=2,
    batch_size=64,
    val_split_file_idxs=[1],
    training={"pretrained_weights": "/data/scratch/zhteoh/730-tutorial/pretrained_weights/sdss_pretrained.pt"}
)

Global seed set to 42

                 from  n    params  module                                  arguments                     
  0                -1  1      3328  yolov5.models.common.Conv               [2, 64, 5, 1]                 
  1                -1  3     12672  yolov5.models.common.Conv               [64, 64, 1, 1]                
  2                -1  1     73984  yolov5.models.common.Conv               [64, 128, 3, 2]               
  3                -1  1    147712  yolov5.models.common.Conv               [128, 128, 3, 1]              
  4                -1  1    295424  yolov5.models.common.Conv               [128, 256, 3, 2]              
  5                -1  6   1118208  yolov5.models.common.C3                 [256, 256, 6]                 
  6                -1  1   1180672  yolov5.models.common.Conv               [256, 512, 3, 2]              
  7                -1  9   6433792  yolov5.models.common.C3                 [512, 512, 9]                 
  8           

Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Epoch 9, global step 20: 'val/loss' reached 0.26338 (best 0.26338), saving model to '/home/zhteoh/730-astropy-integration/output/version_7/checkpoints/epoch=9-val_loss=0.263.ckpt' as top 1


...

Epoch 19, global step 40: 'val/loss' was not in top 1


Validation: 0it [00:00, ?it/s]

Epoch 29, global step 60: 'val/loss' was not in top 1


Validation: 0it [00:00, ?it/s]

Epoch 39, global step 80: 'val/loss' was not in top 1


## Run the model

### Using sample dataset

#### Download the sample dataset

In [12]:
from bliss.surveys.sdss import PhotoFullCatalog, SloanDigitalSkySurvey

sdss_data_path = "/home/zhteoh/730-astropy-integration/data/sdss"
photo_cat = PhotoFullCatalog.from_file(sdss_data_path, run=94, camcol=1, field=12, band=2)
sdss = SloanDigitalSkySurvey(sdss_data_path, 94, 1, (12,), (2,))

#### Get predictions for the sample dataset

In [13]:
from bliss.api import predict_sdss

est_cat, est_cat_table, galaxy_params_table = predict_sdss(
    data_path="/home/zhteoh/730-astropy-integration/case_studies/astropy_integration_730/data/sdss", 
    weight_save_path="/home/zhteoh/730-astropy-integration/case_studies/astropy_integration_730/data/pretrained_models/sdss.pt",
    # predict={"dataset": {"run": 94, "camcol": 1, "fields": [12]}}
)


                 from  n    params  module                                  arguments                     
  0                -1  1      3328  yolov5.models.common.Conv               [2, 64, 5, 1]                 
  1                -1  3     12672  yolov5.models.common.Conv               [64, 64, 1, 1]                
  2                -1  1     73984  yolov5.models.common.Conv               [64, 128, 3, 2]               
  3                -1  1    147712  yolov5.models.common.Conv               [128, 128, 3, 1]              
  4                -1  1    295424  yolov5.models.common.Conv               [128, 256, 3, 2]              
  5                -1  6   1118208  yolov5.models.common.C3                 [256, 256, 6]                 
  6                -1  1   1180672  yolov5.models.common.Conv               [256, 512, 3, 2]              
  7                -1  9   6433792  yolov5.models.common.C3                 [512, 512, 9]                 
  8                -1  1   4720640  

In [14]:
from IPython.display import display
from IPython.core.display import HTML

with open("./predict.html", "r") as f:
    html_str = f.read()
    display(HTML(html_str))

In [15]:
est_cat_table.show_in_notebook(display_length=5)

In [16]:
galaxy_params_table.show_in_notebook(display_length=5)

#### Save predicted catalog to FITS file

In [17]:
est_cat_table.write("est_cat.fits", format="fits")

OSError: File est_cat.fits already exists. If you mean to replace it then use the argument "overwrite=True".

In [18]:
# Check that catalog is saved as intended
from astropy.table import Table

est_cat_table = Table.read("est_cat.fits", format="fits")
est_cat_table.show_in_notebook(display_length=5)

#### Evaluate prediction

In [19]:
import torch

from bliss.metrics import BlissMetrics

est_cat_cuda = est_cat.to(torch.device("cpu"))
photo_cat_cuda = photo_cat.to(torch.device("cpu"))

metrics = BlissMetrics()
results = metrics(est_cat_cuda, photo_cat_cuda)

print(results)

{'detection_precision': tensor(0.), 'detection_recall': tensor(0.), 'f1': tensor(nan), 'avg_distance': tensor(59.98706), 'n_matches': tensor(0), 'n_matches_gal_coadd': tensor(0), 'class_acc': tensor(nan), 'gal_tp': tensor(0), 'gal_fp': tensor(0), 'gal_fn': tensor(0), 'gal_tn': tensor(0)}


### Using user-specified dataset

#### Download online dataset

In [5]:
from astropy.coordinates import SkyCoord
from astroquery.sdss import SDSS
from pathlib import Path

from bliss.api import load_survey

# pos = SkyCoord('0h8m05.63s +14d50m23.3s', frame='icrs') # 1011/3/44
# pos = SkyCoord("1h8m05.73s +13d10m20.3s", frame="icrs") # 4829/5/27
pos = SkyCoord("1h2m05.83s -2d11m20.3s", frame="icrs") # 2699/4/71
region = SDSS.query_region(pos, radius="5 arcsec")
run, camcol, field = region["run"][0], region["camcol"][0], region["field"][0]
print("run:", run, "camcol:", camcol, "field:", field)
load_survey("sdss", run, camcol, field, download_dir=Path("/home/zhteoh/730-astropy-integration/case_studies/astropy_integration_730/data/sdss"))

run: 2699 camcol: 4 field: 71


#### Get predictions for the downloaded dataset

In [8]:
from bliss.api import predict_sdss

est_cat_dl, est_cat_table_dl, galaxy_params_table_dl = predict_sdss(
    data_path="/home/zhteoh/730-astropy-integration/case_studies/astropy_integration_730/data/sdss",
    weight_save_path="/home/zhteoh/730-astropy-integration/case_studies/astropy_integration_730/data/pretrained_models/sdss.pt",
    predict={"dataset": {"run": 1011, "camcol": 3, "fields": [44]}}
)


                 from  n    params  module                                  arguments                     
  0                -1  1      3328  yolov5.models.common.Conv               [2, 64, 5, 1]                 
  1                -1  3     12672  yolov5.models.common.Conv               [64, 64, 1, 1]                
  2                -1  1     73984  yolov5.models.common.Conv               [64, 128, 3, 2]               
  3                -1  1    147712  yolov5.models.common.Conv               [128, 128, 3, 1]              
  4                -1  1    295424  yolov5.models.common.Conv               [128, 256, 3, 2]              
  5                -1  6   1118208  yolov5.models.common.C3                 [256, 256, 6]                 
  6                -1  1   1180672  yolov5.models.common.Conv               [256, 512, 3, 2]              
  7                -1  9   6433792  yolov5.models.common.C3                 [512, 512, 9]                 
  8                -1  1   4720640  

In [9]:
est_cat_table_dl.show_in_notebook(display_length=5)

In [10]:
galaxy_params_table_dl.show_in_notebook(display_length=5)